<a href="https://colab.research.google.com/github/r42arty/hse/blob/main/mod4/DL/DL_3.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Основы машинного обучения, ИИМУП

## НИУ ВШЭ, 2024-25 учебный год

# Домашнее задание 3: Рекуррентные нейронные сети

Задание выполнил(а):

    Рубцов Артемий

## Общая информация

__Внимание!__  


* Домашнее задание выполняется самостоятельно
* Не допускается помощь в решении домашнего задания от однокурсников или третьих лиц. «Похожие» решения считаются плагиатом, и все задействованные студенты — в том числе и те, у кого списали, — не могут получить за него больше 0 баллов
* Использование в решении домашнего задания генеративных моделей (ChatGPT и так далее) за рамками справочной и образовательной информации для генерации кода задания — считается плагиатом, и такое домашнее задание оценивается в 0 баллов
* Старайтесь сделать код как можно более оптимальным. Неэффективная реализация кода может негативно отразиться на оценке. Также оценка может быть снижена за плохо читаемый код и плохо оформленные графики. Все ответы должны сопровождаться кодом или комментариями о том, как они были получены.

### О задании

В этом задании вам предстоит самостоятельно реализовать модель LSTM для решения задачи классификации с пересекающимися классами (multi-label classification). Это вид классификации, в которой каждый объект может относиться одновременно к нескольким классам. Такая задача часто возникает при классификации фильмов по жанрам, научных или новостных статей по темам, музыкальных композиций по инструментам и так далее.

В нашем случае мы будем работать с датасетом биотехнических новостей и классифицировать их по темам. Этот датасет уже предобработан: текст приведен к нижнему регистру, удалена пунктуация, все слова разделены проблелом.

In [1]:
!pip install optuna gensim wandb
!pip install --upgrade numpy gensim

import pandas as pd
import numpy as np
import string
import torch
import nltk
import optuna
import wandb
from torch import nn
from torch.utils.data import Dataset, DataLoader
from torch.nn.utils.rnn import pad_sequence
from torch import optim
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MultiLabelBinarizer
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.linear_model import LogisticRegression
from sklearn.multiclass import OneVsRestClassifier
from sklearn.metrics import f1_score
from collections import Counter, defaultdict
from gensim.corpora import Dictionary
from nltk.corpus import stopwords
from tqdm.notebook import tqdm

optuna.logging.set_verbosity(optuna.logging.WARNING)

  Using cached numpy-2.3.0-cp311-cp311-manylinux_2_28_x86_64.whl.metadata (62 kB)


In [3]:
BIOTECH_NEWS = 'https://www.dropbox.com/scl/fi/v624fdeg3bikyxyvr93i3/biotech_news.tsv?rlkey=iaekqfwtbqswl8vd5dpnd9d92&st=mzgbw5km&dl=1'

In [4]:
dataset = pd.read_csv(BIOTECH_NEWS, sep='\t')
dataset.head()

text labels
0  drive your plow over the bones of the dead by ...  other
1  in the recently tabled national budget denel h...  other
2  shares take a break its good for you picture g...  other
3  reso is currently hiring for two positions pro...  other
4  charter buyer club what is the charter buyer c...  other

## Предобработка лейблов


__Задание 1 (1.5 балла)__. Как вы можете заметить, лейблы записаны в виде строк, разделенных запятыми. Для работы с ними нам нужно преобразовать их в числа. Так как каждый объект может принадлежать нескольким классам, закодируйте лейблы в виде векторов из 0 и 1, где 1 означает, что объект принадлежит соответствующему классу, а 0 – не принадлежит. Имея такую кодировку, мы сможем обучить модель, решая задачу бинарной классификации для каждого класса.

In [5]:
labels = dataset['labels'].apply(lambda x: x.split(','))

mlb = MultiLabelBinarizer()
labels_binary = mlb.fit_transform(labels).astype('float32')

labels_binary_df = pd.DataFrame(labels_binary, columns=mlb.classes_)
labels_binary_df

alliance & partnership   article publication  \
0                         0.0                   0.0   
1                         0.0                   0.0   
2                         0.0                   0.0   
3                         0.0                   0.0   
4                         0.0                   0.0   
...                       ...                   ...   
3034                      0.0                   0.0   
3035                      0.0                   0.0   
3036                      0.0                   0.0   
3037                      0.0                   0.0   
3038                      0.0                   0.0   

       clinical trial sponsorship   closing   company description  \
0                             0.0       0.0                   0.0   
1                             0.0       0.0                   0.0   
2                             0.0       0.0                   0.0   
3                             0.0       0.0                   0.0   
4                             0.0       0.0                   0.0   
...                           ...       ...                   ...   
3034                          0.0       0.0                   0.0   
3035                          0.0       0.0                   0.0   
3036                          0.0       0.0                   1.0   
3037                          0.0       1.0                   1.0   
3038                          0.0       0.0                   0.0   

       department establishment   event organization   executive appointment  \
0                           0.0                  0.0                     0.0   
1                           0.0                  0.0                     0.0   
2                           0.0                  0.0                     0.0   
3                           0.0                  0.0                     0.0   
4                           0.0                  0.0                     0.0   
...                         ...                  ...                     ...   
3034                        0.0                  0.0                     0.0   
3035                        0.0                  0.0                     0.0   
3036                        0.0                  0.0                     0.0   
3037                        0.0                  0.0                     0.0   
3038                        0.0                  0.0                     0.0   

       executive statement   expanding geography  ...  \
0                      0.0                   0.0  ...   
1                      0.0                   0.0  ...   
2                      0.0                   0.0  ...   
3                      0.0                   0.0  ...   
4                      0.0                   0.0  ...   
...                    ...                   ...  ...   
3034                   1.0                   0.0  ...   
3035                   0.0                   0.0  ...   
3036                   1.0                   0.0  ...   
3037                   0.0                   0.0  ...   
3038                   1.0                   0.0  ...   

      new initiatives or programs  other  participation in an event  \
0                             0.0    1.0                        0.0   
1                             0.0    1.0                        0.0   
2                             0.0    1.0                        0.0   
3                             0.0    1.0                        0.0   
4                             0.0    1.0                        0.0   
...                           ...    ...                        ...   
3034                          0.0    0.0                        0.0   
3035                          0.0    0.0                        0.0   
3036                          1.0    0.0                        0.0   
3037                          0.0    0.0                        0.0   
3038                          0.0    0.0                        0.0   

      patent publi

## Предобработка данных

В этом задании мы будем обучать рекуррентные нейронные сети. Как вы знаете, они работают лучше для коротких текстов, так как не очень хорошо улавливают далекие зависимости. Для уменьшение длин текстов их стоит почистить.

Сразу разделим выборку на обучающую и тестовую, чтобы считать все нужные статистики только по обучающей.

In [6]:
from sklearn.model_selection import train_test_split

texts_train, texts_test, y_train, y_test = train_test_split(
    dataset['text'],
    labels_binary,
    test_size=0.2,  # do not change this
    random_state=0,  # do not change this
)

__Задание 2 (1.5 балла)__. Удалите из текстов стоп слова, слишком редкие и слишком частые слова. Гиперпараметры подберите самостоятельно (в идеале их стоит подбирать по качеству на тестовой выборке). Если вы считаете, что стоит добавить еще какую-то обработку, то сделайте это. Важно не удалить ничего, что может повлиять на предсказание класса.

In [7]:
nltk.download('stopwords')
stopwords = set(stopwords.words('english'))

def search_objective(trial):
    min_count = trial.suggest_int("min_count", 2, 10)
    max_count = trial.suggest_float("max_count", 0.3, 0.9)

    train_tokens = texts_train.apply(lambda text: [w for w in text.split() if w not in stopwords])

    freq_counter = Counter()
    for tokens in train_tokens:
        freq_counter.update(tokens)

    doc_count = len(train_tokens)
    too_common = {w for w, f in freq_counter.items() if f > doc_count * max_count}
    too_rare = {w for w, f in freq_counter.items() if f < min_count}

    def filter_tokens(tokens):
        return [w for w in tokens if w not in too_common and w not in too_rare]

    train_clean_texts = train_tokens.apply(filter_tokens).apply(lambda x: ' '.join(x))
    test_clean_texts = texts_test.apply(
        lambda t: ' '.join([w for w in t.split() if w not in stopwords and w not in too_common and w not in too_rare])
    )

    vectorizer = CountVectorizer()
    X_train_bow = vectorizer.fit_transform(train_clean_texts)
    X_test_bow = vectorizer.transform(test_clean_texts)

    model = OneVsRestClassifier(LogisticRegression(max_iter=1000))
    model.fit(X_train_bow, y_train)

    y_pred = model.predict(X_test_bow)
    score = f1_score(y_test, y_pred, average='micro')

    return score


study = optuna.create_study(direction="maximize")
study.optimize(search_objective, n_trials=5)

print("Подобранные параметры:", study.best_params)
print("Самый высокий F1:", study.best_value)

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


Подобранные параметры: {'min_count': 5, 'max_count': 0.8112299300854409}
Самый высокий F1: 0.6074154852780806


In [8]:
# очистка текста
best_min_count = study.best_params['min_count']
best_max_count = study.best_params['max_count']

tokens_train_final = texts_train.apply(lambda t: [w for w in t.split() if w not in stopwords])

final_counter = Counter()
for tokens in tokens_train_final:
    final_counter.update(tokens)

total_docs = len(tokens_train_final)
very_common = {w for w, f in final_counter.items() if f > total_docs * best_max_count}
very_rare = {w for w, f in final_counter.items() if f < best_min_count}

def final_filter(tokens):
    return [w for w in tokens if w not in very_common and w not in very_rare]

clean_train_tokens = tokens_train_final.apply(final_filter)
clean_test_tokens = texts_test.apply(lambda t: final_filter([w for w in t.split() if w not in stopwords]))

train_texts_final = clean_train_tokens.apply(lambda x: ' '.join(x))
test_texts_final = clean_test_tokens.apply(lambda x: ' '.join(x))

__Задание 3 (2 балла)__. Осталось перевести тексты в индексы токенов, чтобы их можно было подавать в модель. У вас есть две опции, как это сделать:
1. __(+0 баллов)__ Токенизировать тексты по словам.
2. __(до +5 баллов)__ Реализовать свою токенизацию BPE. Количество баллов будет варьироваться в зависимости от эффективности реализации. При реализации нельзя пользоваться специализированными библиотеками.

Токенизируйте тексты, переведите их в списки индексов и сложите вместе с лейблами в `DataLoader`. Не забудьте добавить в `DataLoader` `collate_fn`, которая будет дополнять все короткие тексты в батче паддингами. Для маппинга токенов в индексы вам может пригодиться `gensim.corpora.dictionary.Dictionary`.

In [9]:
max_len = 1024

def get_vocab(texts):
    vocab = Counter()
    for text in texts:
        for word in text.split():
            symbols = list(word) + ['</w>']
            vocab[tuple(symbols)] += 1
    return vocab

def get_stats(vocab):
    pairs = defaultdict(int)
    for word, freq in vocab.items():
        for i in range(len(word) - 1):
            pairs[(word[i], word[i+1])] += freq
    return pairs

def merge_vocab(pair, vocab):
    new_vocab = {}
    bigram = ' '.join(pair)
    replacement = ''.join(pair)
    for word, freq in vocab.items():
        w = ' '.join(word)
        w_new = w.replace(bigram, replacement)
        new_vocab[tuple(w_new.split())] = freq
    return new_vocab

def learn_bpe(texts, num_merges=500):
    vocab = get_vocab(texts)
    for _ in range(num_merges):
        pairs = get_stats(vocab)
        if not pairs: break
        best = max(pairs, key=pairs.get)
        vocab = merge_vocab(best, vocab)
    return vocab

texts = dataset['text'].tolist()
bpe_vocab = learn_bpe(texts, num_merges=500)

bpe_tokens = set()
for word in bpe_vocab:
    bpe_tokens.update(word)
bpe_tokens.update(['<BOS>', '<EOS>'])
bpe_tokens = list(bpe_tokens)
print(f"BPE словарь: {len(bpe_tokens)} токенов")

dictionary = Dictionary([bpe_tokens])
print(f"Dictionary size: {len(dictionary)}")

def bpe_tokenize(text, bpe_vocab):
    tokens = ['<BOS>']
    for word in text.split():
        symbols = list(word) + ['</w>']
        while True:
            pairs = [(symbols[i], symbols[i+1]) for i in range(len(symbols)-1)]
            pair_freqs = Counter(pairs)
            best = None
            for pair in pair_freqs:
                if pair in bpe_vocab:
                    best = pair
                    break
            if not best:
                break
            first, second = best
            new_symbols = []
            i = 0
            while i < len(symbols):
                if i < len(symbols)-1 and symbols[i] == first and symbols[i+1] == second:
                    new_symbols.append(first + second)
                    i += 2
                else:
                    new_symbols.append(symbols[i])
                    i += 1
            symbols = new_symbols
        tokens.extend(symbols)
    tokens.append('<EOS>')

    return tokens[:max_len]

tokens_list = []
texts_token_ids = []

for text in tqdm(texts, desc="Tokenizing process"):
    tokens = bpe_tokenize(text, bpe_vocab)
    ids = dictionary.doc2idx(tokens)
    ids = [idx if idx != -1 else 0 for idx in ids]

    tokens_list.append(tokens)
    texts_token_ids.append(ids)

class BPEDataset(Dataset):
    def __init__(self, texts_ids, labels):
        self.texts = texts_ids
        self.labels = labels

    def __len__(self):
        return len(self.texts)

    def __getitem__(self, idx):
        return torch.tensor(self.texts[idx], dtype=torch.long), torch.tensor(self.labels[idx], dtype=torch.float32)

def collate_fn(batch):
    texts, labels = zip(*batch)
    texts_padded = pad_sequence(texts, batch_first=True, padding_value=0)
    labels = torch.stack(labels)
    return texts_padded, labels

train_idx, test_idx = train_test_split(range(len(texts_token_ids)), test_size=0.2, random_state=0)

bpe_dataset = BPEDataset(texts_token_ids, labels_binary_df.values)
train_dataset = torch.utils.data.Subset(bpe_dataset, train_idx)
test_dataset = torch.utils.data.Subset(bpe_dataset, test_idx)

train_loader = DataLoader(train_dataset, batch_size=32, shuffle=True, collate_fn=collate_fn)
test_loader = DataLoader(test_dataset, batch_size=32, shuffle=False, collate_fn=collate_fn)

BPE словарь: 11383 токенов
Dictionary size: 11383


Tokenizing process:   0%|          | 0/3039 [00:00<?, ?it/s]

## Метрика качества

Перед тем, как приступить к обучению, нам нужно выбрать метрику оценки качества. Так как в задаче классификации с пересекающимися классами классы часто несбалансированы, чаще всего в качестве метрики берется [F1 score](https://en.wikipedia.org/wiki/F-score).

Функция `compute_f1` принимает истинные метки и предсказанные и считает среднее значение F1 по всем классам. Используйте ее для оценки качества моделей.

$$
F1_{total} = \frac{1}{K} \sum_{k=1}^K F1(Y_k, \hat{Y}_k),
$$
где $Y_k$ – истинные значения для класса k, а $\hat{Y}_k$ – предсказания.

In [10]:
def compute_f1(y_true, y_pred):
    assert y_true.ndim == 2
    assert y_true.shape == y_pred.shape

    return f1_score(y_true, y_pred, average='macro')

## Обучение моделей

### RNN

В качестве бейзлайна обучим самую простую рекуррентную нейронную сеть. Напомним, что блок RNN выглядит таким образом.

<img src="https://i.postimg.cc/yYbNBm6G/tg-image-1635618906.png" alt="drawing" width="400"/>

Его скрытое состояние обновляется по формуле
$h_t = \sigma(W x_{t} + U h_{t-1} + b_h)$. А предсказание считается с помощью применения линейного слоя к последнему токену
$o_T = V h_T + b_o$. В качестве функции активации выберите гиперболический тангенс.

__Задание 4 (2 балла)__. Реализуйте RNN в соответствии с формулой выше и обучите ее на нашу задачу. Нулевой скрытый вектор инициализируйте нулями, так модель будет обучаться стабильнее, чем при случайной инициализации. После этого замеряйте качество на тестовой выборке. У вас должно получиться значение F1 не меньше 0.33, а само обучение не должно занимать много времени.

In [16]:
class RNN(nn.Module):
    def __init__(self, vocab_size, input_size, hidden_size, num_layers, n_classes):
        super().__init__()
        self.embedding = nn.Embedding(vocab_size, input_size)
        self.rnn = nn.GRU(
            input_size=input_size,
            hidden_size=hidden_size,
            num_layers=num_layers,
            batch_first=True
        )
        self.out_fc = nn.Linear(hidden_size, n_classes)

    def forward(self, input_ids):
        x = self.embedding(input_ids)
        output, _ = self.rnn(x)
        last_hidden = output[:, -1, :]
        logits = self.out_fc(last_hidden)
        return logits

num_pos = (labels_binary_df.values == 1).sum()
num_neg = (labels_binary_df.values == 0).sum()
ratio = num_neg / num_pos
print(f"pos_weight ratio = {ratio:.2f}")

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

def train(model, dataloader, optimizer, criterion):
    model.train()
    for X_batch, y_batch in tqdm(dataloader, desc="Training", leave=False):
        X_batch, y_batch = X_batch.to(device), y_batch.float().to(device)
        optimizer.zero_grad()
        logits = model(X_batch)
        loss = criterion(logits, y_batch)
        loss.backward()
        optimizer.step()

def evaluate(model, dataloader, criterion):
    model.eval()
    losses = []
    all_preds = []
    all_labels = []
    with torch.no_grad():
        for X_batch, y_batch in tqdm(dataloader, desc="Evaluating", leave=False):
            X_batch, y_batch = X_batch.to(device), y_batch.float().to(device)
            logits = model(X_batch)
            loss = criterion(logits, y_batch)
            preds = (torch.sigmoid(logits) >= 0.5).int()
            losses.append(loss.item())
            all_preds.append(preds.cpu())
            all_labels.append(y_batch.cpu())
    mean_loss = np.mean(losses)
    f1 = compute_f1(torch.cat(all_preds).numpy(), torch.cat(all_labels).numpy())
    return f1, mean_loss

def objective(trial):
    input_size = trial.suggest_categorical("input_size", [64, 128, 256])
    hidden_size = trial.suggest_categorical("hidden_size", [64, 128, 256])
    num_layers = trial.suggest_int("num_layers", 1, 3)
    lr = trial.suggest_float("lr", 1e-4, 1e-2, log=True)
    weight_decay = trial.suggest_float("weight_decay", 1e-6, 1e-3, log=True)

    print(f"Trial {trial.number} | input_size: {input_size} | hidden_size: {hidden_size} | num_layers: {num_layers} | lr: {lr:.6f} | weight_decay: {weight_decay:.6f}\n")

    model = RNN(
        vocab_size=len(dictionary),
        input_size=input_size,
        hidden_size=hidden_size,
        num_layers=num_layers,
        n_classes=labels_binary_df.shape[1]
    ).to(device)

    optimizer = optim.Adam(model.parameters(), lr=lr, weight_decay=weight_decay)
    criterion = nn.BCEWithLogitsLoss(pos_weight=torch.tensor([ratio]).to(device))

    best_f1 = 0
    patience = 5
    patience_counter = 0

    scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(
        optimizer, mode='max', factor=0.5, patience=2
    )

    for epoch in range(10):
        train(model, train_loader, optimizer, criterion)
        test_f1, _ = evaluate(model, test_loader, criterion)
        scheduler.step(test_f1)

        if test_f1 > best_f1:
            best_f1 = test_f1
            patience_counter = 0
        else:
            patience_counter += 1
            if patience_counter >= patience:
                break

    return best_f1

study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=20)

print("Лучшие параметры:", study.best_params)
print("Лучший F1:", study.best_value)

pos_weight ratio = 29.06
Trial 0 | input_size: 128 | hidden_size: 256 | num_layers: 2 | lr: 0.000511 | weight_decay: 0.000018



Training:   0%|          | 0/76 [00:00<?, ?it/s]

Evaluating:   0%|          | 0/19 [00:00<?, ?it/s]

/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


Training:   0%|          | 0/76 [00:00<?, ?it/s]

...

/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


Training:   0%|          | 0/76 [00:00<?, ?it/s]

Evaluating:   0%|          | 0/19 [00:00<?, ?it/s]

Лучшие параметры: {'input_size': 128, 'hidden_size': 256, 'num_layers': 2, 'lr': 0.002556360558473557, 'weight_decay': 3.750802003433225e-05}
Лучший F1: 0.26115208307913396


/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


In [19]:
best_params = study.best_params

model = RNN(
    vocab_size=len(dictionary),
    input_size=best_params["input_size"],
    hidden_size=best_params["hidden_size"],
    num_layers=best_params["num_layers"],
    n_classes=labels_binary_df.shape[1]
).to(device)

optimizer = optim.Adam(
    model.parameters(),
    lr=best_params["lr"],
    weight_decay=best_params["weight_decay"]
)

criterion = nn.BCEWithLogitsLoss(pos_weight=torch.tensor([ratio]).to(device))

scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(
    optimizer, mode='max', factor=0.5, patience=2
)

best_f1 = 0
patience = 10
patience_counter = 0

for epoch in tqdm(range(50), desc="Epochs"):
    train(model, train_loader, optimizer, criterion)
    test_f1, test_loss = evaluate(model, test_loader, criterion)

    # Логирование вручную
    print(f"Эпоха {epoch+1}: test_loss = {test_loss:.4f}, test_f1 = {test_f1:.4f}")

    scheduler.step(test_f1)

    if test_f1 > best_f1:
        best_f1 = test_f1
        patience_counter = 0
        torch.save(model.state_dict(), "best_rnn.pt")
    else:
        patience_counter += 1
        if patience_counter >= patience:
            print(f"Ранняя остановка на эпохе {epoch+1} — улучшений нет.")
            break

Epochs:   0%|          | 0/50 [00:00<?, ?it/s]

Training:   0%|          | 0/76 [00:00<?, ?it/s]

Evaluating:   0%|          | 0/19 [00:00<?, ?it/s]

Эпоха 1: test_loss = 0.9446, test_f1 = 0.0537


/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


...

/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


Training:   0%|          | 0/76 [00:00<?, ?it/s]

Evaluating:   0%|          | 0/19 [00:00<?, ?it/s]

Эпоха 30: test_loss = 3.1374, test_f1 = 0.3130
Ранняя остановка на эпохе 30 — улучшений нет.


/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


### LSTM

<img src="https://i.postimg.cc/pL5LdmpL/tg-image-2290675322.png" alt="drawing" width="400"/>

Теперь перейдем к более продвинутым рекурренным моделям, а именно LSTM. Из-за дополнительного вектора памяти эта модель должна гораздо лучше улавливать далекие зависимости, что должно напрямую отражаться на качестве.

Параметры блока LSTM обновляются вот так ($\sigma$ означает сигмоиду):
\begin{align}
f_{t} &= \sigma(W_f x_{t} + U_f h_{t-1} + b_f) \\
i_{t} &= \sigma(W_i x_{t} + U_i h_{t-1} + b_i) \\
\tilde{c}_{t} &= \tanh(W_c x_{t} + U_c h_{t-1} + b_i) \\
c_{t} &= f_t \odot c_{t-1} + i_t \odot \tilde{c}_t \\
o_{t} &= \sigma(W_t x_{t} + U_t h_{t-1} + b_t) \\
h_t &= o_t \odot \tanh(c_t)
\end{align}

__Задание 5 (2 балла).__ Реализуйте LSTM по описанной схеме. Выберите гиперпараметры LSTM так, чтобы их общее число (без учета слоя эмбеддингов) примерно совпадало с числом параметров обычной RNN, но размерность скрытого слоя была не меньше 64. Так мы будем сравнивать архитектуры максимально независимо. Обучите LSTM до сходимости и сравните качество с RNN на тестовой выборке. Удалось ли получить лучший результат? Как вы можете это объяснить?

In [21]:
class LSTM(nn.Module):
    def __init__(self, vocab_size, input_size=128, hidden_size=128, num_layers=1, n_classes=labels_binary_df.shape[1], dropout=0.3):
        super().__init__()
        self.embedding = nn.Embedding(vocab_size, input_size)
        self.lstm = nn.LSTM(
            input_size=input_size,
            hidden_size=hidden_size,
            num_layers=num_layers,
            dropout=dropout if num_layers > 1 else 0.0,
            batch_first=True
        )
        self.out_fc = nn.Linear(hidden_size, n_classes)

    def forward(self, input_ids):
        x = self.embedding(input_ids)
        output, (h_n, c_n) = self.lstm(x)
        last_hidden = output[:, -1, :]
        logits = self.out_fc(last_hidden)
        return logits


num_pos = (labels_binary_df.values == 1).sum()
num_neg = (labels_binary_df.values == 0).sum()
ratio = num_neg / num_pos
print(f"pos_weight ratio = {ratio:.2f}")

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

model = LSTM(
    vocab_size=len(dictionary),
    input_size=best_params["input_size"],
    hidden_size=best_params["hidden_size"],
    num_layers=best_params["num_layers"],
    n_classes=labels_binary_df.shape[1],
    dropout=0.3
).to(device)

optimizer = optim.Adam(model.parameters(), lr=1e-3, weight_decay=1e-5)
criterion = nn.BCEWithLogitsLoss(pos_weight=torch.tensor([ratio]).to(device))


def train(model, dataloader, optimizer, criterion):
    model.train()
    for X_batch, y_batch in tqdm(dataloader, desc="Training", leave=False):
        X_batch, y_batch = X_batch.to(device), y_batch.float().to(device)
        optimizer.zero_grad()
        logits = model(X_batch)
        loss = criterion(logits, y_batch)
        loss.backward()
        torch.nn.utils.clip_grad_norm_(model.parameters(), max_norm=1.0)
        optimizer.step()


def evaluate(model, dataloader, criterion):
    model.eval()
    losses = []
    all_preds = []
    all_labels = []
    with torch.no_grad():
        for X_batch, y_batch in tqdm(dataloader, desc="Evaluating", leave=False):
            X_batch, y_batch = X_batch.to(device), y_batch.float().to(device)
            logits = model(X_batch)
            loss = criterion(logits, y_batch)
            preds = (torch.sigmoid(logits) >= 0.5).int()
            losses.append(loss.item())
            all_preds.append(preds.cpu())
            all_labels.append(y_batch.cpu())
    mean_loss = np.mean(losses)
    f1 = compute_f1(torch.cat(all_preds).numpy(), torch.cat(all_labels).numpy())

    # Простое логирование
    print(f"Test Loss: {mean_loss:.4f}, Test F1: {f1:.4f}")

    return f1, mean_loss


scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(
    optimizer, mode='max', factor=0.5, patience=2, verbose=True
)

best_f1 = 0
patience = 10
patience_counter = 0

for epoch in tqdm(range(50), desc="Epochs"):
    train(model, train_loader, optimizer, criterion)
    test_f1, test_loss = evaluate(model, test_loader, criterion)
    scheduler.step(test_f1)

    if test_f1 > best_f1:
        best_f1 = test_f1
        patience_counter = 0
        torch.save(model.state_dict(), "best_lstm.pt")
        print(f"Модель сохранена на эпохе {epoch+1} с F1: {test_f1:.4f}")
    else:
        patience_counter += 1
        if patience_counter >= patience:
            print(f"Ранняя остановка на эпохе {epoch+1} — улучшений нет.")
            break

pos_weight ratio = 29.06


Epochs:   0%|          | 0/50 [00:00<?, ?it/s]

Training:   0%|          | 0/76 [00:00<?, ?it/s]

Evaluating:   0%|          | 0/19 [00:00<?, ?it/s]

Test Loss: 0.9244, Test F1: 0.0440
Модель сохранена на эпохе 1 с F1: 0.0440


...

/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


Training:   0%|          | 0/76 [00:00<?, ?it/s]

Evaluating:   0%|          | 0/19 [00:00<?, ?it/s]

Test Loss: 3.0946, Test F1: 0.2386


/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


__Задание 6 (1 балл).__ В этом задании у вас есть две опции на выбор: добавить __двунаправленность__ для LSTM _или_ добавить __многослойность__. Можно сделать и то, и другое, но дополнительных баллов за это мы не дадим, только бесконечный респект. Обе модификации реализуются довольно просто (буквально 4 строчки кода, если вы аккуратно реализовали модель) и дают примерно одинаковый прирост в качестве. Сделайте выводы: стоит ли увеличивать размер модели в несколько раз?

In [22]:
class LSTM(nn.Module):
    def __init__(self, vocab_size, input_size=128, hidden_size=128, num_layers=1, n_classes=labels_binary_df.shape[1], dropout=0.3):
        super().__init__()
        self.embedding = nn.Embedding(vocab_size, input_size)
        self.lstm = nn.LSTM(
            input_size=input_size,
            hidden_size=hidden_size,
            num_layers=num_layers,
            dropout=dropout if num_layers > 1 else 0.0,
            batch_first=True,
            bidirectional=True
        )
        self.out_fc = nn.Linear(hidden_size * 2, n_classes)

    def forward(self, input_ids):
        x = self.embedding(input_ids)
        output, _ = self.lstm(x)
        last_hidden = output[:, -1, :]
        logits = self.out_fc(last_hidden)
        return logits


# Вычисляем pos_weight
num_pos = (labels_binary_df.values == 1).sum()
num_neg = (labels_binary_df.values == 0).sum()
ratio = num_neg / num_pos
print(f"pos_weight ratio = {ratio:.2f}")

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Инициализация модели
model = LSTM(
    vocab_size=len(dictionary),
    input_size=best_params["input_size"],
    hidden_size=best_params["hidden_size"],
    num_layers=best_params["num_layers"],
    n_classes=labels_binary_df.shape[1],
    dropout=0.3
).to(device)

optimizer = optim.Adam(model.parameters(), lr=1e-3, weight_decay=1e-5)
criterion = nn.BCEWithLogitsLoss(pos_weight=torch.tensor([ratio]).to(device))


def train(model, dataloader, optimizer, criterion):
    model.train()
    for X_batch, y_batch in tqdm(dataloader, desc="Training", leave=False):
        X_batch, y_batch = X_batch.to(device), y_batch.float().to(device)
        optimizer.zero_grad()
        logits = model(X_batch)
        loss = criterion(logits, y_batch)
        loss.backward()
        torch.nn.utils.clip_grad_norm_(model.parameters(), max_norm=1.0)
        optimizer.step()


def evaluate(model, dataloader, criterion):
    model.eval()
    losses = []
    all_preds = []
    all_labels = []
    with torch.no_grad():
        for X_batch, y_batch in tqdm(dataloader, desc="Evaluating", leave=False):
            X_batch, y_batch = X_batch.to(device), y_batch.float().to(device)
            logits = model(X_batch)
            loss = criterion(logits, y_batch)
            preds = (torch.sigmoid(logits) >= 0.5).int()
            losses.append(loss.item())
            all_preds.append(preds.cpu())
            all_labels.append(y_batch.cpu())
    mean_loss = np.mean(losses)
    f1 = compute_f1(torch.cat(all_preds).numpy(), torch.cat(all_labels).numpy())

    # Выводим метрики в консоль
    print(f"Test Loss: {mean_loss:.4f}, Test F1: {f1:.4f}")

    return f1, mean_loss


# Планировщик
scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(
    optimizer, mode='max', factor=0.5, patience=2, verbose=True
)

best_f1 = 0
patience = 10
patience_counter = 0

# Тренировка модели
for epoch in tqdm(range(50), desc="Epochs"):
    print(f"\nЭпоха {epoch+1}")
    train(model, train_loader, optimizer, criterion)
    test_f1, test_loss = evaluate(model, test_loader, criterion)
    scheduler.step(test_f1)

    if test_f1 > best_f1:
        best_f1 = test_f1
        patience_counter = 0
        torch.save(model.state_dict(), "best_lstm.pt")
        print(f"Модель сохранена — F1: {test_f1:.4f}")
    else:
        patience_counter += 1
        if patience_counter >= patience:
            print(f"Ранняя остановка на эпохе {epoch+1} — улучшений нет.")
            break

pos_weight ratio = 29.06


/usr/local/lib/python3.11/dist-packages/torch/optim/lr_scheduler.py:62: UserWarning: The verbose parameter is deprecated. Please use get_last_lr() to access the learning rate.
  warnings.warn(


Epochs:   0%|          | 0/50 [00:00<?, ?it/s]


Эпоха 1


Training:   0%|          | 0/76 [00:00<?, ?it/s]

...

/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


Training:   0%|          | 0/76 [00:00<?, ?it/s]

Evaluating:   0%|          | 0/19 [00:00<?, ?it/s]

Test Loss: 4.0713, Test F1: 0.2815
Модель сохранена — F1: 0.2815


/usr/local/lib/python3.11/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
